In [1]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
import tensorflow_datasets as tfds
from tensorflow.keras.layers import Dense, Input, Conv2D, MaxPooling2D, Flatten, BatchNormalization,Dropout
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Layer, RandomFlip, RandomRotation, Rescaling, Resizing, InputLayer, Input
from tensorflow.keras.metrics import Accuracy,BinaryCrossentropy, FalsePositives, FalseNegatives, TruePositives, TrueNegatives, Precision, Recall,AUC, BinaryAccuracy
from sklearn.metrics import confusion_matrix, roc_curve
import seaborn as sns
from tensorflow.keras.callbacks import Callback, CSVLogger, EarlyStopping, LearningRateScheduler, ModelCheckpoint, ReduceLROnPlateau
import pandas as pd
from tensorflow.keras.regularizers import L2, L1
import cv2
import tensorflow_probability as tfp
import albumentations as A
import datetime
from tensorboard import notebook
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.layers import LeakyReLU
import io
from tensorboard.plugins.hparams import api as hp
import wandb

In [2]:
import os
os.chdir("/Users/admin/Downloads")
os.getcwd()

'/Users/admin/Downloads'

In [3]:
dataset, dataset_info = tfds.load('malaria', with_info = True, as_supervised = True, shuffle_files = True, split = ['train'])

INFO:absl:Load dataset info from /Users/admin/tensorflow_datasets/malaria/1.0.0
INFO:absl:Reusing dataset malaria (/Users/admin/tensorflow_datasets/malaria/1.0.0)
INFO:absl:Creating a tf.data.Dataset reading 4 files located in folders: /Users/admin/tensorflow_datasets/malaria/1.0.0.
INFO:absl:Constructing tf.data.Dataset malaria for split ['train'], from /Users/admin/tensorflow_datasets/malaria/1.0.0


In [4]:
def split(dataset, Train_ratio, Val_ratio, Test_ratio):
    Dataset_size = len(dataset)
    
    train_dataset = dataset.take(int(Train_ratio*Dataset_size))
    print(list(train_dataset.as_numpy_iterator()))
    
    val_test_dataset = dataset.skip(int(Train_ratio*Dataset_size))
    val_dataset = val_test_dataset.take(int(Val_ratio*Dataset_size))
    print(list(val_dataset.as_numpy_iterator()))
    
    test_dataset = val_test_dataset.skip(int(Val_ratio*Dataset_size))
    print(list(test_dataset.as_numpy_iterator()))
    return train_dataset, val_dataset, test_dataset

In [5]:
Train_ratio = 0.8
Val_ratio = 0.1
Test_ratio = 0.1

In [8]:
train_dataset, val_dataset, test_dataset = split(dataset[0], Train_ratio, Val_ratio, Test_ratio)

2024-08-14 23:22:23.037197: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

2024-08-14 23:22:27.278726: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


[(array([[[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       ...,

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]]], dtype=uint8), 1), (array([[[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
      

2024-08-14 23:22:29.661877: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [12]:
len(train_dataset), len(val_dataset), len(test_dataset)

(22046, 2755, 2757)

# Preprocess the data

In [15]:
IM_SIZE = 224

def resize_rescale(image, label):
    return tf.image.resize(image, (IM_SIZE,IM_SIZE))/255.0, label

In [17]:
def visualize(original, augmented):
    plt.subplot(1,2,1)
    plt.imshow(original)

    plt.subplot(1,2,2)
    plt.imshow(augmented)

In [19]:
def parasite_or_not(x):
    if (x < 0.5):
       return str('P')
    else:
      return str('U')

In [21]:
resize_rescale_layers = tf.keras.Sequential([
    Resizing(224, 224),
    Rescaling(1.0 / 255)
])

# Function to apply resize and rescale
def resize_and_rescale(image, label):
    image = resize_rescale_layers(image)
    return image, label

In [23]:
def augment_layers(image, label):

    image, label = resize_rescale(image,label)

    image = tf.image.rot90(image)
    image = tf.image.flip_left_right(image)

    return image, label

In [25]:
class RotNinety(Layer):
    def __init__(self):
        super().__init__()
        
    @tf.function
    def call(self, image):
       return tf.image.rot90(image,k = tf.random.uniform(shape = [], minval = 0, maxval = 2, dtype = tf.int32))

In [27]:
augment_layers = tf.keras.Sequential([
    RotNinety(),
    RandomFlip(mode='horizontal')
])

# Function to apply resize, rescale, and augmentation

def resize_rescale_and_augment(image, label):
    image = resize_rescale_layers(image)
    image = augment_layers(image, training=True)
    return image, label

# Callbacks

In [30]:
class LogImagesCallbackWandB(tf.keras.callbacks.Callback):
    def on_epoch_end(self, epoch, logs=None):
        # Convert the test dataset to numpy arrays
        test_images, test_labels = zip(*[(image.numpy(), label.numpy()) for image, label in test_dataset])

        # Remove the extra dimension if it exists
        test_images = np.squeeze(np.array(test_images))
        test_labels = np.array(test_labels)

        # Make predictions
        pred = lenet_model_2.predict(test_images)
        prediction = pred[:, 0]
        
        threshold = 0.5
        

        wandb.log({'Confusion Matrix' : wandb.plot.confusion_matrix(
            probs = prediction,
            y_true =test_labels,
            class_names = ["Parasitized", "Uninfected"])})

In [32]:
class LogImagesCallbackWandB(tf.keras.callbacks.Callback):
    def on_epoch_end(self, epoch, logs=None):
        # Convert the test dataset to numpy arrays
        test_images, test_labels = zip(*[(image.numpy(), label.numpy()) for image, label in test_dataset])

        # Remove the extra dimension if it exists
        test_images = np.squeeze(np.array(test_images))
        test_labels = np.array(test_labels)

        # Make predictions
        pred = lenet_model_2.predict(test_images)
        prediction = (pred[:, 0] > 0.5).astype(int)

        wandb.log({'Confusion Matrix' : wandb.plot.confusion_matrix(
            preds = prediction,
            y_true = test_labels,
            class_names = ["Parasitized", "Uninfected"])})


In [34]:
class LogImagesCallbackWandB(Callback):
  def on_epoch_end(self, epoch, logs):
    labels = []
    inp = []

    for x,y in test_dataset.as_numpy_iterator():
      labels.append(y)
      inp.append(x)
    labels = np.array([i[0] for i in labels])
    predicted = lenet_model.predict(np.array(inp)[:,0,...])

    threshold = 0.5

    cm = confusion_matrix(labels, predicted > threshold)
    
    plt.figure(figsize=(8,8))

    sns.heatmap(cm, annot=True,)
    plt.title('Confusion matrix - {}'.format(threshold))
    plt.ylabel('Actual')
    plt.xlabel('Predicted')
    plt.axis('off')

    buffer = io.BytesIO()
    plt.savefig(buffer, format = 'png')

    image_array = tf.image.decode_png(buffer.getvalue(), channels=3)

    images = wandb.Image(image_array, caption="Confusion Matrix for epoch: {}".format(epoch))
          
    wandb.log(
        {"Confusion Matrix": images})

In [36]:
es_callback = EarlyStopping(monitor = 'val_loss', min_delta = 0, patience = 2, verbose = 0,
                            mode = 'auto', baseline = None, restore_best_weights=False)

In [38]:
checkpoint = ModelCheckpoint(
    filepath = "/Users/admin/Downloads/save_model.keras", monitor = 'val_loss', save_best_only = True, mode = 'auto',
    save_freq = 'epoch')

In [40]:
plateau_callback = ReduceLROnPlateau(
    monitor = 'val_accuracy', factor = 0.1, patience = 2, verbose = 1)

# Custom Loss Method

In [43]:
bce = BinaryCrossentropy()
def custom_bce(y_true, y_pred):
    return bce(y_true,y_pred)

In [45]:
def custom_accuracy(Factor):
    def metric(y_true, y_pred):
        return tf.keras.metrics.binary_accuracy(y_true, y_pred)*Factor
    return metric

In [47]:
class CustomAccuracy(tf.keras.metrics.Metric):
    def __init__(self, factor, name='custom_accuracy', **kwargs):
        super(CustomAccuracy, self).__init__(name=name, **kwargs)
        self.factor = factor
        self.total_accuracy = self.add_weight(name='total_accuracy', initializer='zeros')
        self.count = self.add_weight(name='count', initializer='zeros')

    def update_state(self, y_true, y_pred, sample_weight=None):
        y_true = tf.reshape(y_true, tf.shape(y_pred))
        accuracy = tf.keras.metrics.binary_accuracy(y_true, y_pred)
        self.total_accuracy.assign_add(tf.reduce_sum(accuracy * self.factor))
        self.count.assign_add(tf.cast(tf.size(accuracy), tf.float32))

    def result(self):
        return self.total_accuracy / self.count

    def reset_states(self):
        self.total_accuracy.assign(0)
        self.count.assign(0)


In [49]:
class CustomBCE(tf.keras.losses.Loss):
    def __init__(self, name="custom_bce"):
        super(CustomBCE, self).__init__(name=name)
        self.bce = tf.keras.losses.BinaryCrossentropy()

    def call(self, y_true, y_pred):
        # Ensure y_true and y_pred have the same shape
        y_true = tf.reshape(y_true, tf.shape(y_pred))
        
        # Calculate binary crossentropy
        return self.bce(y_true, y_pred)


# Models

In [137]:
train_dataset, val_dataset, test_dataset = split(dataset[0], Train_ratio, Val_ratio, Test_ratio)

2024-08-15 02:00:22.842391: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

2024-08-15 02:00:27.028377: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


[(array([[[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       ...,

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]]], dtype=uint8), 1), (array([[[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
        ...,
        [0, 0, 0],
        [0, 0, 0],
        [0, 0, 0]],

       [[0, 0, 0],
        [0, 0, 0],
        [0, 0, 0],
      

2024-08-15 02:00:29.610772: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [138]:
Batch_size = 32
train_dataset = (
    train_dataset
    .shuffle(buffer_size = 8, reshuffle_each_iteration = True)
    .map(resize_and_rescale)
    .batch(Batch_size)
    .prefetch(tf.data.AUTOTUNE)
)

In [139]:
Batch_size = 32
val_dataset = (
    val_dataset
    .shuffle(buffer_size = 8, reshuffle_each_iteration = True)
    .map(resize_and_rescale)
    .batch(Batch_size)
    .prefetch(tf.data.AUTOTUNE)
)

In [140]:
test_dataset = test_dataset.map(resize_and_rescale, num_parallel_calls = tf.data.AUTOTUNE)
test_dataset = test_dataset.batch(1)

In [56]:
print(train_dataset)
print(val_dataset)
print(test_dataset)

<_PrefetchDataset element_spec=(TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None), TensorSpec(shape=(None,), dtype=tf.int64, name=None))>
<_PrefetchDataset element_spec=(TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None), TensorSpec(shape=(None,), dtype=tf.int64, name=None))>
<_BatchDataset element_spec=(TensorSpec(shape=(None, 224, 224, 3), dtype=tf.float32, name=None), TensorSpec(shape=(None,), dtype=tf.int64, name=None))>


In [ ]:
IM_SIZE = 224
DROPOUT_RATE = 0.2
REGULARIZATION_RATE = 0.01


lenet_model_2 = tf.keras.Sequential([
    InputLayer(input_shape = (IM_SIZE, IM_SIZE, 3)),

    Conv2D(filters = 6 , kernel_size = 3, strides = 1 , padding='valid',
          activation = 'relu',kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D (pool_size = 2, strides= 2),
    Dropout(rate = DROPOUT_RATE ),

    Conv2D(filters = 16, kernel_size = 3, strides=1, padding='valid',
          activation = 'relu', kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D (pool_size = 2, strides= 2),

    Flatten(),
    
    Dense(128, activation = "relu", kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    Dropout(rate = DROPOUT_RATE),
    
    Dense(16, activation = "relu", kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),

    Dense(1, activation = "sigmoid"),

])


In [ ]:
metrics = [TruePositives(name = 'TP'), FalsePositives(name = 'FP'), TrueNegatives(name = 'TN'), FalseNegatives(name = 'FN'), 
           BinaryAccuracy(name = 'accuracy'), Precision(name = 'precision'), Recall(name = 'recall'), AUC(name = 'auc')]

In [ ]:
lenet_model_2.compile(optimizer = Adam(0.0001),
                    loss = CustomBCE(),
                    metrics = metrics)
history= lenet_model_2.fit(train_dataset, validation_data = val_dataset, epochs = 1, verbose = 1, callbacks = [tensorboard_callback])

In [ ]:
history= lenet_model_2.fit(train_dataset, validation_data = val_dataset, epochs = 1, verbose = 1, callbacks = [tensorboard_callback])

# Tensorboard

In [ ]:
!rm -rf ./logs/

In [62]:
CURRENT_TIME = datetime.datetime.now().strftime('%d%m%y - %h%m%s')
METRIC_DIR = './logs/' + CURRENT_TIME + '/metrics'
print(METRIC_DIR)
train_writer = tf.summary.create_file_writer(METRIC_DIR)

./logs/140824 - Aug081723699376/metrics


In [64]:
CURRENT_TIME = datetime.datetime.now().strftime('%Y%m%d-%H%M%S')
log_dir = "./logs/" + CURRENT_TIME
profiler_dir = log_dir + "/train"

# Start the profiler
tf.profiler.experimental.start(profiler_dir)

# TensorBoard callback with profiling
tensorboard_callback = tf.keras.callbacks.TensorBoard(
    log_dir=log_dir, 
    histogram_freq=1, 
    profile_batch='100,132'
)

history= lenet_model_2.fit(train_dataset, validation_data = val_dataset, epochs = 1, verbose = 1, callbacks = [tensorboard_callback])

tf.profiler.experimental.stop()

2024-08-14 23:22:57.049036: I external/local_tsl/tsl/profiler/lib/profiler_session.cc:104] Profiler session initializing.
2024-08-14 23:22:57.049064: I external/local_tsl/tsl/profiler/lib/profiler_session.cc:119] Profiler session started.
ERROR:root:Failed to start profiler: Another profiler is running.


NameError: name 'lenet_model_2' is not defined

In [ ]:
log_dir = "./logs"
tensorboard_callback = tf.keras.callbacks.TensorBoard(
    log_dir=log_dir, 
    histogram_freq=1)

In [ ]:
def scheduler(epoch, lr):
    if epoch < 1:
      learning_rate =  lr
    else:
      learning_rate =  lr * tf.math.exp(-0.1).numpy()
    with train_writer.as_default():
        tf.summary.scalar('Learning Rate', data = learning_rate, step = epoch)
    return learning_rate


In [ ]:
scheduler_callback = LearningRateScheduler(scheduler, verbose = 1)

In [ ]:
import tensorflow as tf

log_dir = "./logs"
profiler_dir = log_dir + "/train"
tf.profiler.experimental.start(profiler_dir)

# Your training code here

tf.profiler.experimental.stop()


In [ ]:
%reload_ext tensorboard
%tensorboard --logdir ./logs

# Custom Training Loops

In [ ]:
CURRENT_TIME = datetime.datetime.now().strftime('%d%m%y - %h%m%s')
CUSTOM_TRAIN_DIR = './logs/' + CURRENT_TIME + '/custom/train'
CUSTOM_VAL_DIR = './logs/' + CURRENT_TIME + '/custom/val'

custom_train_writer = tf.summary.create_file_writer(CUSTOM_TRAIN_DIR)
custom_val_writer = tf.summary.create_file_writer(CUSTOM_VAL_DIR)

In [ ]:
def training_block(x_batch, y_batch, model, metric, loss_function):
    with tf.GradientTape() as recorder:
        y_pred = model(x_batch, training=True)
        y_batch = tf.reshape(y_batch, y_pred.shape)
        loss = loss_function(y_batch, y_pred)
        
        #wand.log({'loss' : loss.numpy()})
        partial_derivatives = recorder.gradient(loss, model.trainable_weights)

        # Check for None gradients
        for grad, var in zip(partial_derivatives, model.trainable_weights):
            if grad is None:
                tf.print(f"Gradient for {var.name} is None. Check the connection of this layer to the loss.")

        if any([g is None for g in partial_derivatives]):
            tf.print("Some gradients are None. Check the model and loss function.")
        else:
            global_optimizer.apply_gradients(zip(partial_derivatives, model.trainable_weights))
            metric.update_state(y_batch, y_pred)

    return loss

@tf.function
def validation_block(x_batch_val, y_batch_val, model, val_metric, loss_function):
    y_pred_val = model(x_batch_val, training=False)
    y_batch_val = tf.reshape(y_batch_val, y_pred_val.shape)
    val_loss = loss_function(y_batch_val, y_pred_val)
    val_metric.update_state(y_batch_val, y_pred_val)
    return val_loss


In [ ]:
def neuralearn(model, loss_function, metric, val_metric, train_dataset, val_dataset, epochs, val_steps):
    for epoch in range(epochs):
        print(f"Training starts for epoch number {epoch + 1}")

        # Training loop
        for step, (x_batch, y_batch) in enumerate(train_dataset):
            loss = training_block(x_batch, y_batch, model, metric, loss_function)

            # Print loss at every specified step
            if (step + 1) % 689 == 0:
                print(f"Step {step + 1}, Loss: {loss.numpy()}")
                print("Training accuracy is: ", metric.result().numpy())
                
                with custom_train_writer.as_default():
                   tf.summary.scalar('Training Loss', data = loss, step = epoch)

                with custom_train_writer.as_default():
                   tf.summary.scalar('Training Accuracy', data = metric.result(), step = epoch)
                
                metric.reset_state()

        # Validation loop
        for step, (x_batch_val, y_batch_val) in enumerate(val_dataset):
            val_loss = validation_block(x_batch_val, y_batch_val, model, val_metric, loss_function)

            # Print validation loss and accuracy at every val_steps
            if (step + 1) % val_steps == 0:
                print("Validation Loss: {}".format(val_loss.numpy()))
                print("Validation accuracy is: ", val_metric.result().numpy())

                with custom_val_writer.as_default():
                   tf.summary.scalar('Validation Loss', data = val_loss, step = epoch)

                with custom_val_writer.as_default():
                   tf.summary.scalar('Validation Accuracy', data = val_metric.result(), step = epoch)

                
                val_metric.reset_state()

        print(f"Epoch {epoch + 1} completed")
    print("Training is complete")

In [ ]:
EPOCHS = NUM_EPOCHS
VAL_STEPS = 86
custom_bce = CustomBCE()  # Custom BCE loss with factor 1.0
metric = BinaryAccuracy()
val_metric = BinaryAccuracy()
global_optimizer = Adam(0.01)

In [ ]:
neuralearn(lenet_model_2, custom_bce, metric, val_metric, train_dataset, val_dataset, EPOCHS, VAL_STEPS)

In [ ]:
import matplotlib.pyplot as plt

In [ ]:

plt.plot(history.history['accuracy'], c = 'r')
plt.plot(history.history['val_accuracy'], c= 'b')
plt.title('Model Accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend(['train','val'])
plt.show()

In [ ]:
plt.figure(figsize = (6,6))
plt.plot(history.history['loss'], c = 'r')
plt.plot(history.history['val_loss'], c = 'b')
plt.title('Model Loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.show()

In [ ]:
# Now, evaluate the model
lenet_model_2.evaluate(test_dataset)



In [ ]:
test_images, test_labels = zip(*[(image.numpy(), label.numpy()) for image, label in test_dataset])

# Convert lists to numpy arrays if needed
test_images = np.array(test_images)
test_labels = np.array(test_labels)
print(test_images.shape)

In [ ]:
pred=lenet_model_2.predict(test_images[:,0,...])
pred

In [ ]:
prediction =pred[:,0]

In [ ]:
threshold = 0.5

cm = confusion_matrix(labels, prediction > threshold)

In [ ]:
plt.figure(figsize = (4,4))
sns.heatmap(cm, annot = True)
plt.title('Confusion Matrix - {}'.format(threshold))
plt.ylabel('Actual')
plt.xlabel('Predicted')

plt.show()

In [ ]:
fp, tp, threshold = roc_curve(labels, prediction)
len(fp), len(tp), len(threshold)

In [ ]:
plt.figure(figsize = (6,6))
plt.plot(fp, tp)
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')

plt.grid()

skip = 50
for i in range(0, len(threshold), skip):
    plt.text(fp[i], tp[i], threshold[i])
    
plt.show()

In [ ]:
list1 = [1, 2, 3]
list2 = ['a', 'b', 'c']


In [ ]:
combined = zip(list1, list2)
print(list(combined))


# Hyperparameter tuning

In [ ]:
IM_SIZE = 224

def model_tune(hparams):

    lenet_model_2 = tf.keras.Sequential([
        InputLayer(input_shape=(IM_SIZE, IM_SIZE, 3)),
    
        Conv2D(filters=6, kernel_size=3, strides=1, padding='valid',
               activation='relu', kernel_regularizer=L2(hparams[HP_REGULARIZATION_RATE])),
        BatchNormalization(),
        MaxPooling2D(pool_size=2, strides=2),
        Dropout(rate=hparams[HP_DROPOUT]),
    
        Conv2D(filters=16, kernel_size=3, strides=1, padding='valid',
               activation='relu', kernel_regularizer=L2(hparams[HP_REGULARIZATION_RATE])),
        BatchNormalization(),
        MaxPooling2D(pool_size=2, strides=2),
    
        Flatten(),
        
        Dense(hparams[HP_NUM_UNITS_1], activation='relu', kernel_regularizer=L2(hparams[HP_REGULARIZATION_RATE])),
        BatchNormalization(),
        Dropout(rate=hparams[HP_DROPOUT]),
        
        Dense(hparams[HP_NUM_UNITS_2], activation='relu', kernel_regularizer=L2(hparams[HP_REGULARIZATION_RATE])),
        BatchNormalization(),
    
        Dense(1, activation='sigmoid'),
    ])

    lenet_model_2.compile(optimizer=Adam(learning_rate=hparams[HP_LEARNING_RATE]),
                          loss='binary_crossentropy',
                          metrics=['accuracy'])

    lenet_model_2.fit(val_dataset, epochs=1)
    _, accuracy = lenet_model_2.evaluate(val_dataset)
    return accuracy


In [ ]:
HP_NUM_UNITS_1 = hp.HParam('num_units_1', hp.Discrete([16,32,64,128]))
HP_NUM_UNITS_2 = hp.HParam('num_units_2', hp.Discrete([16,32,64,128]))
HP_DROPOUT = hp.HParam('dropout_rate', hp.Discrete([0.1,0.2,0.3]))
HP_REGULARIZATION_RATE = hp.HParam('regularization_rate', hp.Discrete([0.001, 0.01, 0.1]))
HP_LEARNING_RATE = hp.HParam('learning_rate', hp.Discrete([1e-4, 1e-3]))

In [ ]:
run_number = 1
for num_units_1 in HP_NUM_UNITS_1.domain.values:
    for num_units_2 in HP_NUM_UNITS_2.domain.values:
        for dropout_rate in HP_DROPOUT.domain.values:
            for regularization_rate in HP_REGULARIZATION_RATE.domain.values:
                for learning_rate in HP_LEARNING_RATE.domain.values:

                    # Ensure hparams are defined only once
                    hparams = {
                        HP_NUM_UNITS_1: num_units_1,
                        HP_NUM_UNITS_2: num_units_2,
                        HP_DROPOUT: dropout_rate,
                        HP_REGULARIZATION_RATE: regularization_rate,
                        HP_LEARNING_RATE: learning_rate,
                    }

                    file_writer = tf.summary.create_file_writer('logs/' + str(run_number))

                    with file_writer.as_default():
                        hp.hparams(hparams)  # Log the hyperparameters
                        accuracy = model_tune(hparams)
                        tf.summary.scalar('accuracy', accuracy, step=run_number)
                    
                    print(f"For run {run_number}, hparams: num_units_1:{num_units_1}, num_units_2:{num_units_2}, "
                          f"dropout:{dropout_rate}, regularization_rate:{regularization_rate}, learning_rate:{learning_rate}")
                    
                    run_number += 1


In [ ]:
%reload_ext tensorboard
%tensorboard --logdir ./logs

# Wandb Install and Login

In [ ]:
#wandb.tensorboard.patch(root_dir = "./logs")
wandb.init(project = 'Malaria-Tensorboard')

In [ ]:
class LogImagesCallbackWandB(Callback):
  def on_epoch_end(self, epoch, logs):
    labels = []
    inp = []

    for x,y in test_dataset.as_numpy_iterator():
      labels.append(y)
      inp.append(x)
    labels = np.array([i[0] for i in labels])
    predicted = lenet_model_2.predict(np.array(inp)[:,0,...])

    threshold = 0.5

    cm = confusion_matrix(labels, predicted > threshold)
    
    plt.figure(figsize=(8,8))

    sns.heatmap(cm, annot=True,)
    plt.title('Confusion matrix - {}'.format(threshold))
    plt.ylabel('Actual')
    plt.xlabel('Predicted')
    plt.axis('off')

    buffer = io.BytesIO()
    plt.savefig(buffer, format = 'png')

    image_array = tf.image.decode_png(buffer.getvalue(), channels=3)

    images = wandb.Image(image_array, caption="Confusion Matrix for epoch: {}".format(epoch))
          
    wandb.log(
        {"Confusion Matrix": images})



In [82]:
from wandb.integration.keras import WandbMetricsLogger

In [ ]:
WandbMetricsLogger = WandbMetricsLogger()

In [66]:
metrics = [TruePositives(name = 'TP'), FalsePositives(name = 'FP'), TrueNegatives(name = 'TN'), FalseNegatives(name = 'FN'), 
           BinaryAccuracy(name = 'accuracy'), Precision(name = 'precision'), Recall(name = 'recall'), AUC(name = 'auc')]
LABELS = ['Parasitized', 'Uninfected']

In [ ]:
wandb.config = {
    "learning_rate" : 0.001,
    "epochs" : 100, 
    "batch_size" : 128,
    "DROPOUT_RATE" : 0.0,
    "IM_SIZE" : 224,
    "REGULARIZATION_RATE" : 0.0,
    "N_FILTERS" : 6,
    "KERNEL_SIZE" : 6,
    "N_STRIDES" : 3,
    "POOL_SIZE" : 2,
    "N_DENSE_1" : 128,
    "N_DENSE_2" : 32,
    "LEARNING_RATE" : 0.0001,
    "NUM_EPOCHS": 3
} 


In [ ]:
CONFIGURATION = wandb.config

IM_SIZE = CONFIGURATION["IM_SIZE"]
DROPOUT_RATE = CONFIGURATION["DROPOUT_RATE"]
REGULARIZATION_RATE = CONFIGURATION["REGULARIZATION_RATE"]
N_FILTERS = CONFIGURATION["N_FILTERS"]
KERNEL_SIZE = CONFIGURATION["KERNEL_SIZE"]
POOL_SIZE = CONFIGURATION["POOL_SIZE"]
N_STRIDES = CONFIGURATION["N_STRIDES"]
LEARNING_RATE = CONFIGURATION['LEARNING_RATE'] 
NUM_EPOCHS = CONFIGURATION['NUM_EPOCHS'] 


lenet_model_2 = tf.keras.Sequential([
    Input(shape = (IM_SIZE, IM_SIZE, 3)),

    Conv2D(filters = N_FILTERS , kernel_size = KERNEL_SIZE, strides = N_STRIDES , padding='valid',
          activation = 'relu',kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D (pool_size = POOL_SIZE, strides= N_STRIDES),
    Dropout(rate = DROPOUT_RATE ),

    Conv2D(filters = N_FILTERS, kernel_size = KERNEL_SIZE, strides= N_STRIDES, padding='valid',
          activation = 'relu', kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D (pool_size = POOL_SIZE, strides= N_STRIDES),

    Flatten(),
    
    Dense(N_FILTERS, activation = "relu", kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),
    Dropout(rate = DROPOUT_RATE),
    
    Dense( N_FILTERS, activation = "relu", kernel_regularizer = L2(REGULARIZATION_RATE)),
    BatchNormalization(),

    Dense(1, activation = "sigmoid"),

])

In [ ]:
lenet_model_2.compile(optimizer = Adam(learning_rate = LEARNING_RATE),
                    loss = CustomBCE(),
                    metrics = metrics)

In [ ]:
history = lenet_model_2.fit(
    train_dataset, 
    validation_data=val_dataset, 
    epochs=NUM_EPOCHS, 
    verbose=1, 
    callbacks=[LogImagesCallbackWandB(),tensorboard_callback]
)

In [ ]:
lenet_model_2.evaluate(test_dataset)

In [80]:
wandb.finish()

In [ ]:
pred = []

for i in range(len(prediction)):
    if (prediction[i] < 0.5):
        pred.append([1,0])
    else:
        pred.append([0,1])

print(pred)

In [ ]:
print(np.array(pred).shape)

# Hyperparameter tuning 

In [ ]:
wandb.finish()

In [68]:
sweep_config = {
    "name" : "Malaria-Prediction-Sweep",
    "method" : "random",
    "metric": {
        "name" : "accuracy",
        "goal" : "maximize", 
    },
    "parameters" : {
        "N_DENSE_1" : {
            "values" : [16,32,64,128] 
        }, 
         "N_DENSE_2" : {
            "values" : [16,32,64,128] 
         },

         "DROPOUT_RATE" : {
            "min" : 0.1,
            "max" : 0.4
         }, 
         
        "REGULARIZATION_RATE" : {
            "distribution" : "uniform",
            "min" : 0.001,
            "max" : 0.01
         }, 
         
        "LEARNING_RATE" : {
            "distribution" : "uniform",
            "min" : 0.0001,
            "max" : 0.01
         }
    }
} 

        

sweep_id = wandb.sweep(sweep_config)

ERROR:wandb.jupyter:Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.


Create sweep with ID: awkdoywp
Sweep URL: https://wandb.ai/zamir2017-ahmad-vvision-/uncategorized/sweeps/awkdoywp


In [120]:
def model_tune(config):
  lenet_model = tf.keras.Sequential([
    Input(shape = (224, 224, 3)),

    Conv2D(filters = 6 , kernel_size = 3, strides = 1 , padding='valid',
          activation = 'relu',kernel_regularizer = L2(config.REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D(pool_size = 1, strides= 2),
    Dropout(rate = config.DROPOUT_RATE ),

    Conv2D(filters = 16, kernel_size = 3, strides = 1, padding='valid',
          activation = 'relu', kernel_regularizer = L2(config.REGULARIZATION_RATE)),
    BatchNormalization(),
    MaxPooling2D(pool_size = 1, strides= 2),

    Flatten(),
    
    Dense(config.N_DENSE_1, activation = "relu", kernel_regularizer = L2(config.REGULARIZATION_RATE)),
    BatchNormalization(),
    Dropout(rate = config.DROPOUT_RATE),
    
    Dense(config.N_DENSE_2, activation = "relu", kernel_regularizer = L2(config.REGULARIZATION_RATE)),
    BatchNormalization(),

    Dense(1, activation = "sigmoid"),

  ])


  return lenet_model

In [122]:
wandb.config = {
    "LEARNING_RATE" : 0.001,
    "epochs" : 100, 
    "batch_size" : 128,
    "DROPOUT_RATE" : 0.0,
    "IM_SIZE" : 224,
    "REGULARIZATION_RATE" : 0.0,
    "N_FILTERS" : 6,
    "KERNEL_SIZE" : 6,
    "N_STRIDES" : 3,
    "POOL_SIZE" : 2,
    "N_DENSE_1" : 128,
    "N_DENSE_2" : 32,
    "LEARNING_RATE" : 0.0001,
    "NUM_EPOCHS": 3
} 

CONFIGURATION = wandb.config

In [116]:
wandb.finish()

In [124]:
def train():
    with wandb.init(project='lets do it', config=CONFIGURATION) as run:
        config = wandb.config
        model = model_tune(config)
        model.compile(optimizer=Adam(learning_rate=config.LEARNING_RATE), 
                      loss='binary_crossentropy', 
                      metrics=['accuracy'])
        model.fit(val_dataset, epochs=config.NUM_EPOCHS, callbacks=[WandbMetricsLogger()])

count = 5
wandb.agent(sweep_id, function=train, count=count)


wandb: Agent Starting Run: 68kcr1hb with config:
wandb: 	DROPOUT_RATE: 0.26168411091349897
wandb: 	LEARNING_RATE: 0.008682157754468458
wandb: 	N_DENSE_1: 64
wandb: 	N_DENSE_2: 16
wandb: 	REGULARIZATION_RATE: 0.00714099685572521
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Epoch 1/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 198ms/step - accuracy: 0.5647 - loss: 10.5007
Epoch 2/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 208ms/step - accuracy: 0.7232 - loss: 2.6763
Epoch 3/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 18s 179ms/step - accuracy: 0.8258 - loss: 1.9536


wandb: Agent Starting Run: meebxu9p with config:
wandb: 	DROPOUT_RATE: 0.24599321476077063
wandb: 	LEARNING_RATE: 0.001530960852379556
wandb: 	N_DENSE_1: 32
wandb: 	N_DENSE_2: 128
wandb: 	REGULARIZATION_RATE: 0.009817308811637664
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Epoch 1/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 200ms/step - accuracy: 0.5645 - loss: 2.3272
Epoch 2/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 17s 174ms/step - accuracy: 0.6363 - loss: 1.6845
Epoch 3/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 17s 174ms/step - accuracy: 0.6627 - loss: 1.4989


wandb: Agent Starting Run: rytmlciv with config:
wandb: 	DROPOUT_RATE: 0.3805346522898928
wandb: 	LEARNING_RATE: 0.007557086330762199
wandb: 	N_DENSE_1: 64
wandb: 	N_DENSE_2: 16
wandb: 	REGULARIZATION_RATE: 0.0024947236424765597
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Epoch 1/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 182ms/step - accuracy: 0.5974 - loss: 5.5527
Epoch 2/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 19s 194ms/step - accuracy: 0.6156 - loss: 2.0791
Epoch 3/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 212ms/step - accuracy: 0.6395 - loss: 1.6451


wandb: Agent Starting Run: 95l1asz9 with config:
wandb: 	DROPOUT_RATE: 0.26968399164107393
wandb: 	LEARNING_RATE: 0.001795929768890682
wandb: 	N_DENSE_1: 128
wandb: 	N_DENSE_2: 32
wandb: 	REGULARIZATION_RATE: 0.009670284588721816
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Epoch 1/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 19s 191ms/step - accuracy: 0.5787 - loss: 5.1757
Epoch 2/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 205ms/step - accuracy: 0.6225 - loss: 2.8387
Epoch 3/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 20s 213ms/step - accuracy: 0.6608 - loss: 2.5577


wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: ouje1j9j with config:
wandb: 	DROPOUT_RATE: 0.2971044808594653
wandb: 	LEARNING_RATE: 0.007521578159942611
wandb: 	N_DENSE_1: 32
wandb: 	N_DENSE_2: 16
wandb: 	REGULARIZATION_RATE: 0.003764761488553158
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


Epoch 1/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 16s 155ms/step - accuracy: 0.5518 - loss: 4.2199
Epoch 2/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 16s 169ms/step - accuracy: 0.6170 - loss: 1.6309
Epoch 3/3
87/87 ━━━━━━━━━━━━━━━━━━━━ 18s 192ms/step - accuracy: 0.6199 - loss: 1.6446


In [96]:
wandb.finish()

# Wandb Dataset Versioning

In [135]:
dataset, dataset_info = tfds.load('malaria', with_info = True, as_supervised = True, shuffle_files = True, split = ['train'])


INFO:absl:Load dataset info from /Users/admin/tensorflow_datasets/malaria/1.0.0
INFO:absl:Reusing dataset malaria (/Users/admin/tensorflow_datasets/malaria/1.0.0)
INFO:absl:Creating a tf.data.Dataset reading 4 files located in folders: /Users/admin/tensorflow_datasets/malaria/1.0.0.
INFO:absl:Constructing tf.data.Dataset malaria for split ['train'], from /Users/admin/tensorflow_datasets/malaria/1.0.0


In [157]:
print(dataset)

[<_PrefetchDataset element_spec=(TensorSpec(shape=(None, None, 3), dtype=tf.uint8, name=None), TensorSpec(shape=(), dtype=tf.int64, name=None))>]


In [167]:
k = 0
for image, label in dataset[0]:
    with open(f'dataset/malaria_dataset_{k}.npz', mode='wb') as file:
        np.savez(file, image=image.numpy(), label=label.numpy())
    k += 1
    if (k % 1000 == 0):
       print(k)

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000


2024-08-15 02:35:53.008167: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


In [169]:
def load_original_data():
    
    with wandb.init(project = "Malaria-Detection") as run:
        
        original_data = wandb.Artifact(
        name = "new_dataset", 
        type = 'raw_data',
        description = 'The Malaria Dataset',
        metadata = {'source' : 'TFDS',
            'version' : '1.0.0',
            'download_size' : '337.08MIB'
           }
        )
        
        
        original_data.add_dir('dataset/')


        
        with original_data.new_file('original_data.npz', mode = 'wb') as file:
            np.savez(file, dataset)
    
        run.log_artifact(original_data)

In [171]:
load_original_data()

wandb: WARNING Ignored wandb.init() arg project when running a sweep.


wandb: Adding directory to artifact (./dataset)... Exception ignored in: <function ZipFile.__del__ at 0x10597b060>
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.12/zipfile/__init__.py", line 1940, in __del__
    self.close()
  File "/opt/anaconda3/lib/python3.12/zipfile/__init__.py", line 1957, in close
    self.fp.seek(self.start_dir)
ValueError: seek of closed file
Exception ignored in: <function ZipFile.__del__ at 0x10597b060>
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.12/zipfile/__init__.py", line 1940, in __del__
    self.close()
  File "/opt/anaconda3/lib/python3.12/zipfile/__init__.py", line 1957, in close
    self.fp.seek(self.start_dir)
ValueError: seek of closed file
Done. 10.5s
Traceback (most recent call last):
  File "/var/folders/92/_kz_fht558b0hh0627_7zzk00000gn/T/ipykernel_60937/2741727981.py", line 21, in load_original_data
    np.savez(file, dataset)
  File "/opt/anaconda3/lib/python3.12/site-packages/numpy/lib/npyio.

InvalidArgumentError: Cannot convert a Tensor of dtype variant to a NumPy array.